In [1]:
# First we set the corresponding working directory

# path for Alejandra
setwd("/Users/ale/Documents/thesis_codon_bias/Testing_the_TEH/Rscripts")

# Installing all necessary packages
# install.packages("RColorBrewer")
# install.packages("seqinr")
# install.packages("VGAM")
# install.packages("doSNOW")
# install.packages("coda")
# install.packages("EMCluster")
# install.packages("Biostrings")
# if (!requireNamespace("BiocManager", quietly = TRUE))
#   install.packages("BiocManager")
# # Need 3.14 with R version 4.1
# BiocManager::install(version = "3.14")
# BiocManager::install(c("GeneGA"))
# BiocManager::install("sscu")
# install.packages("bioseq")
# install.packages("GeneGA")
# install.packages("AnaCoDa")

# load necessary pacakges
library("RColorBrewer")
library("seqinr")
library("VGAM")
library("doSNOW")
library("coda")
library("EMCluster")
library("Biostrings")
library("bioseq")
library("GeneGA")
library("AnaCoDa")

Warning message:
"le package 'RColorBrewer' a 'et'e compil'e avec la version R 4.1.2"
Warning message:
"le package 'seqinr' a 'et'e compil'e avec la version R 4.1.2"
Warning message:
"le package 'VGAM' a 'et'e compil'e avec la version R 4.1.2"
Le chargement a n'ecessit'e le package : stats4

Le chargement a n'ecessit'e le package : splines

Warning message:
"le package 'doSNOW' a 'et'e compil'e avec la version R 4.1.2"
Le chargement a n'ecessit'e le package : foreach

Warning message:
"le package 'foreach' a 'et'e compil'e avec la version R 4.1.2"
Le chargement a n'ecessit'e le package : iterators

Warning message:
"le package 'iterators' a 'et'e compil'e avec la version R 4.1.2"
Le chargement a n'ecessit'e le package : snow


Attachement du package : 'coda'


L'objet suivant est masqu'e depuis 'package:VGAM':

    nvar


Warning message:
"le package 'EMCluster' a 'et'e compil'e avec la version R 4.1.2"
Le chargement a n'ecessit'e le package : MASS

Warning message:
"le package 'MASS' 

In [2]:
# Source file containing sequence conversion functions
source("sequence_conversions.R")

# Source model functions
source("utils.R")

In [3]:
# Read file and assign to variable
data_ecoli <- read.csv("/Users/ale/Documents/thesis_codon_bias/Testing_the_TEH/data/data_gfp_zrinka.csv", header = TRUE, sep = ",")

# Keep only the columns of interest: 'X...sequence_name...', 'strain...', 'fluorescence.value..AU.' and 'outlier_status..logica.'
data_ecoli <- data_ecoli[,c(1,2,4,5)]

In [4]:
# Store outliers in a separate dataframe
data_ecoli_no_outliers <- data_ecoli[data_ecoli$outlier_status..logica. == "no",]

In [5]:
# Apply function add.mean.fluo.col to calculate and add a mean florescence column to dataframe. This function also renames columns and removes control sequence
data_ecoli <- add.mean.fluo.col(data_ecoli)
data_ecoli_no_outliers <- add.mean.fluo.col(data_ecoli_no_outliers)

In [6]:
# Read sequence constructs file
sequence_constructs <- read.csv("../data/sequence_names_mRNA.csv")

# Add sequence_id column by construct name to the sequence_constructs dataframe
sequence_constructs$sequence_id <- sapply(strsplit(sequence_constructs$Construct.name, "_"), "[", 1)

In [7]:
# Add sequence_id column to dataframe
data_ecoli$sequence_id <- sapply(strsplit(data_ecoli$sequence_name, "-"), "[", 1)
# dataframe with no outliers
data_ecoli_no_outliers$sequence_id <- sapply(strsplit(data_ecoli_no_outliers$sequence_name, "-"), "[", 1)

# Add sequence column from sequence_constructs to dataframe mapping via sequence_id
data_ecoli <- merge(data_ecoli, sequence_constructs[,c(4,5)], by = "sequence_id")
# dataframe with no outliers
data_ecoli_no_outliers <- merge(data_ecoli_no_outliers, sequence_constructs[,c(4,5)], by = "sequence_id")

#### Retrieve Ribosome Overhead Costs

In [8]:
# Retrieve the Ribosome Overhead Costs per codon
roc_ecoli_table <- read.csv("/Users/ale/Documents/thesis_codon_bias/Testing_the_TEH/data/roc_ecoli_table.csv")
roc_ecoli_table

# Store the columns "Codon" and "Mean" in a new vector
roc_codon_ecoli <- roc_ecoli_table$Mean
names(roc_codon_ecoli) <- roc_ecoli_table$Codon
roc_codon_ecoli

X   AA  Codon Mean       Std.Dev     X2.50.     X97.50.   
1   GCA A   GCA   0.19525035 0.011326149 0.17349340 0.2191333 
2   GCC A   GCC   0.43186597 0.015135036 0.40019864 0.4585636 
3   GCG A   GCG   0.29998705 0.011814578 0.27796733 0.3250804 
4   GCT A   GCT   0.00000000 0.000000000 0.00000000 0.0000000 
5   TGC C   TGC   0.00000000 0.000000000 0.00000000 0.0000000 
6   TGT C   TGT   0.16718509 0.027449076 0.11333271 0.2242850 
7   GAC D   GAC   0.00000000 0.000000000 0.00000000 0.0000000 
8   GAT D   GAT   0.31745051 0.013703146 0.29216386 0.3461722 
9   GAA E   GAA   0.00000000 0.000000000 0.00000000 0.0000000 
10  GAG E   GAG   0.19724978 0.012133917 0.17293824 0.2218469 
11  TTC F   TTC   0.00000000 0.000000000 0.00000000 0.0000000 
12  TTT F   TTT   0.63633549 0.023033666 0.59157243 0.6833111 
13  GGA G   GGA   1.08744641 0.038942571 1.01459007 1.1648732 
14  GGC G   GGC   0.15950789 0.009568892 0.14197137 0.1787511 
15  GGG G   GGG   0.77403498 0.027878766 0.72120003 0.8288071 
16  GGT G   GGT   0.00000000 0.000000000 0.00000000 0.0000000 
17  CAC H   CAC   0.00000000 0.000000000 0.00000000 0.0000000 
18  CAT H   CAT   0.56234211 0.024606152 0.51390508 0.6098830 
19  ATA I   ATA   1.54981656 0.057840922 1.43831851 1.6650076 
20  ATC I   ATC   0.00000000 0.000000000 0.00000000 0.0000000 
21  ATT I   ATT   0.39327122 0.014439303 0.36760477 0.4227246 
22  AAA K   AAA   0.00000000 0.000000000 0.00000000 0.0000000 
23  AAG K   AAG   0.08018727 0.012321155 0.05676176 0.1040298 
24  CTA L   CTA   0.97951186 0.034673367 0.91287573 1.0479397 
25  CTC L   CTC   0.32258270 0.023041392 0.26979482 0.3662121 
26  CTG L   CTG   0.00000000 0.000000000 0.00000000 0.0000000 
27  CTT L   CTT   0.51628530 0.022226379 0.46284313 0.5557438 
28  TTA L   TTA   0.92218228 0.031678328 0.86390058 0.9880615 
29  TTG L   TTG   0.69231613 0.021704796 0.64977470 0.7333593 
30  ATG M   ATG   0.00000000          NA         NA        NA 
... ... ... ...   ...        ...         ...        ...       
32  AAT N   AAT   0.70479457 0.02583768  0.65408943 0.75439150
33  CCA P   CCA   0.25630253 0.02425315  0.21114301 0.30333399
34  CCC P   CCC   1.18233104 0.04020904  1.10164255 1.25933235
35  CCG P   CCG   0.00000000 0.00000000  0.00000000 0.00000000
36  CCT P   CCT   0.38413560 0.02359928  0.33729029 0.43166724
37  CAA Q   CAA   0.39821670 0.01864460  0.36516659 0.43878699
38  CAG Q   CAG   0.00000000 0.00000000  0.00000000 0.00000000
39  AGA R   AGA   1.54016434 0.08618825  1.38464820 1.71645534
40  AGG R   AGG   1.93811010 0.12173804  1.70094255 2.15809736
41  CGA R   CGA   1.53859687 0.05619943  1.43812877 1.64607252
42  CGC R   CGC   0.30686827 0.01406061  0.28031239 0.33468337
43  CGG R   CGG   1.62489366 0.05606282  1.51441118 1.73012550
44  CGT R   CGT   0.00000000 0.00000000  0.00000000 0.00000000
45  TCA S   TCA   0.76011651 0.03435615  0.69430718 0.82763010
46  TCC S   TCC   0.10924135 0.01409032  0.08125201 0.13695170
47  TCG S   TCG   0.70481530 0.02929680  0.64457756 0.75828689
48  TCT S   TCT   0.00000000 0.00000000  0.00000000 0.00000000
49  ACA T   ACA   0.77957513 0.03571614  0.70634498 0.84745359
50  ACC T   ACC   0.15474740 0.01269435  0.13024730 0.18068560
51  ACG T   ACG   0.64836901 0.02564133  0.59633660 0.69676923
52  ACT T   ACT   0.00000000 0.00000000  0.00000000 0.00000000
53  GTA V   GTA   0.07026956 0.01082801  0.04974484 0.09178697
54  GTC V   GTC   0.41242085 0.01680620  0.37960407 0.44583718
55  GTG V   GTG   0.32279353 0.01397026  0.29442199 0.34940163
56  GTT V   GTT   0.00000000 0.00000000  0.00000000 0.00000000
57  TGG W   TGG   0.00000000         NA          NA         NA
58  TAC Y   TAC   0.00000000 0.00000000  0.00000000 0.00000000
59  TAT Y   TAT   0.40736776 0.01914421  0.36792176 0.44420524
60  AGC Z   AGC   0.00000000 0.00000000  0.00000000 0.00000000
61  AGT Z   AGT   0.54756951 0.02863847  0.49027952 0.60136712

GCA        GCC        GCG        GCT        TGC        TGT        GAC 
0.19525035 0.43186597 0.29998705 0.00000000 0.00000000 0.16718509 0.00000000 
       GAT        GAA        GAG        TTC        TTT        GGA        GGC 
0.31745051 0.00000000 0.19724978 0.00000000 0.63633549 1.08744641 0.15950789 
       GGG        GGT        CAC        CAT        ATA        ATC        ATT 
0.77403498 0.00000000 0.00000000 0.56234211 1.54981656 0.00000000 0.39327122 
       AAA        AAG        CTA        CTC        CTG        CTT        TTA 
0.00000000 0.08018727 0.97951186 0.32258270 0.00000000 0.51628530 0.92218228 
       TTG        ATG        AAC        AAT        CCA        CCC        CCG 
0.69231613 0.00000000 0.00000000 0.70479457 0.25630253 1.18233104 0.00000000 
       CCT        CAA        CAG        AGA        AGG        CGA        CGC 
0.38413560 0.39821670 0.00000000 1.54016434 1.93811010 1.53859687 0.30686827 
       CGG        CGT        TCA        TCC        TCG        TCT        ACA 
1.62489366 0.00000000 0.76011651 0.10924135 0.70481530 0.00000000 0.77957513 
       ACC        ACG        ACT        GTA        GTC        GTG        GTT 
0.15474740 0.64836901 0.00000000 0.07026956 0.41242085 0.32279353 0.00000000 
       TGG        TAC        TAT        AGC        AGT 
0.00000000 0.00000000 0.40736776 0.00000000 0.54756951

#### Retrieve elongation times

In [9]:
# Retrieve Elongation Rates
# Read the elongation rates file
# Elongation rates are stored in file "data_ecoli_shah2010plosgen.csv" under $Rc
ecoli_codon_data = read.csv(file = "../data/data_ecoli_shah2010plosgen.csv", header = TRUE)

In [10]:
# Assign elongation rates (units: amino acids per second [aa/s])
elongation_rates_ecoli <- ecoli_codon_data$Rc
names(elongation_rates_ecoli) <- mrna.string.to.seq.string(ecoli_codon_data$Codon)

In [11]:
# Assign elongation times
# Elongation times = 1/elongation rates (units: seconds per amino acids [s/aa])
elongation_times_ecoli <- 1 / elongation_rates_ecoli
elongation_times_ecoli

GCA        GCC        GCG        GCT        TGC        TGT        GAC 
0.04652028 0.03674039 0.07267442 0.04532886 0.13960631 0.21815009 0.04653760 
       GAT        GAA        GAG        TTC        TTT        GGA        GGC 
0.07271670 0.03490401 0.05453752 0.06980803 0.10907504 0.13921760 0.03034717 
       GGG        GGT        CAC        CAT        ATA        ATC        ATT 
0.08501233 0.04417351 0.13960631 0.21815009 0.02725910 0.04646624 0.07254262 
       AAA        AAG        CTA        CTC        CTG        CTT        TTA 
0.02326880 0.03635835 0.13910140 0.08713078 0.03008152 0.11238481 0.13945056 
       TTG        ATG        AAC        AAT        CCA        CCC        CCG 
0.08500510 0.01745170 0.03490401 0.05453752 0.13945056 0.08722959 0.08509914 
       CCT        CAA        CAG        AGA        AGG        CGA        CGC 
0.11253657 0.06976420 0.04256587 0.13952839 0.08509914 0.05814292 0.05452563 
       CGG        CGT        TCA        TCC        TCG        TCT        ACA 
0.04105596 0.03489792 0.13937282 0.05368551 0.08507018 0.07423905 0.13927577 
       ACC        ACG        ACT        GTA        GTC        GTG        GTT 
0.05367398 0.05286250 0.07421701 0.02791659 0.02792282 0.04361289 0.03262004 
       TGG        TAC        TAT        AGC        AGT 
0.13960631 0.04653760 0.07271670 0.13960631 0.21815009

#### Computing equations

In [12]:
# This function computes the energy expenditure of a given mRNA sequence, 
# it takes the sum of the elongation times of the codons in the sequence 
# and multiplies it by the sum of the Ribosome Overhead Costs (ROC) of the codons in the same sequence
energy.expenditure.of.mRNA <- function(seq_cand, roc_codon, elongation_times) {
    codons_of_sequence <- seq.string.to.cod.string(seq_cand)
    L <- length(codons_of_sequence)
    
    # Exclude the last codon (stop codon)
    codons <- codons_of_sequence[1:(L-1)]
    
    # Identify positions of codons in the elongation times table
    positions_in_table <- match(codons, names(elongation_times))
    
    # Retrieve elongation times for codons
    elong_times <- elongation_times[positions_in_table]
  
    # Calculate total elongation time
    total_elong_time <- sum(elong_times)

    # Identify positions of codons in the ROC table
    positions_in_table <- match(codons, names(roc_codon))

    # Retrieve ROC for codons
    roc_codon <- roc_codon[positions_in_table]

    # Calculate total roc
    total_roc <- sum(roc_codon)
    
    # Calculate energy expenditure of the mRNA sequence
    energy_expenditure <- total_elong_time * total_roc
    
    return(energy_expenditure)
}

In [13]:
# Test the function translation.success.rate.of.mRNA
seq_cand <- sequence_constructs$Sequence[1]
energy.expenditure.of.mRNA(seq_cand, roc_codon_ecoli, elongation_times_ecoli)

[1] 3785.051

In [14]:
# Create a funciton that add energy expenditure column to dataframe
add.energy.exp <- function(data, roc_codon, elongation_times){
  data$energy_expenditure <- sapply(data$Sequence, energy.expenditure.of.mRNA, roc_codon = roc_codon_ecoli, elongation_times = elongation_times_ecoli)
  return(data)
}

In [15]:
data_ecoli <- add.energy.exp(data_ecoli, roc_codon_ecoli, elongation_times_ecoli)
data_ecoli_no_outliers <- add.energy.exp(data_ecoli_no_outliers, roc_codon_ecoli, elongation_times_ecoli)

In [16]:
# Read the nonsense error rates file
# Nonsense error rates obtained from FONSE model are stored in file "nonsense_error_rates_fonse.csv" under "$Mean"
ecoli_nonsense_error_data = read.csv(file = "/Users/ale/Documents/thesis_codon_bias/Testing_the_TEH/Rscripts/nonsense_error_rates_fonse.csv", header = TRUE)

In [17]:
# Assign nonsense error rates values to the corresponding codon and create a new vector containing all values
nonsense_error_rates_ecoli <- ecoli_nonsense_error_data$Mean
names(nonsense_error_rates_ecoli) <- ecoli_nonsense_error_data$Codon

In [18]:
# function to compute the accuracy part of the equation 
product.of.q1s <- function(seq_cand, nonsense_error_rates_ecoli, verbose = FALSE) {
  codons_of_sequence <- seq.string.to.cod.string(seq_cand)
  L <- length(codons_of_sequence)
  
  if (verbose) {
    cat("length candidate sequence is:", L, '\n')
  }
  
  # Exclude the last codon (stop codon)
  codons <- codons_of_sequence[1:(L-1)]
  
  # Identify positions of codons in the nonsense error rate table
  positions_in_table <- match(codons, names(nonsense_error_rates_ecoli))

  # Retrieve nonsense error rates for codons
  error_rate_mRNA <- nonsense_error_rates_ecoli[positions_in_table]
  
  # Calculate total translation success rate of the mRNA sequence
  prod_q1 <- prod(1-error_rate_mRNA)^-1
  return(prod_q1)
}

In [19]:
# This function adds the total success rate column to dataframe
add.prod.q1 <- function(data, nonsense_error_rates_ecoli){
  data$prod_q1 <- sapply(data$Sequence, product.of.q1s, nonsense_error_rates_ecoli = nonsense_error_rates_ecoli)
  return(data)
}

In [20]:
data_ecoli <- add.prod.q1(data_ecoli, nonsense_error_rates_ecoli)
data_ecoli_no_outliers <- add.prod.q1(data_ecoli_no_outliers, nonsense_error_rates_ecoli)

In [21]:
data_ecoli
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

In [22]:
# function to compute the total nonsense errors of the sequence
qi <- function(seq_cand, nonsense_error_rates_ecoli, verbose = FALSE) {
  codons_of_sequence <- seq.string.to.cod.string(seq_cand)
  L <- length(codons_of_sequence)
  
  if (verbose) {
    cat("length candidate sequence is:", L, '\n')
  }
  
  # Exclude the last codon (stop codon)
  codons <- codons_of_sequence[1:(L-1)]
  
  # Identify positions of codons in the nonsense error rate table
  positions_in_table <- match(codons, names(nonsense_error_rates_ecoli))

  # Retrieve nonsense error rates for codons
  error_rate_mRNA <- nonsense_error_rates_ecoli[positions_in_table]

  # Calculate total translation success rate of the mRNA sequence
  qi <- sum(error_rate_mRNA)
  return(qi)
}

In [23]:
# This function adds the total success rate column to dataframe
add.qi <- function(data, nonsense_error_rates_ecoli){
  data$qi <- sapply(data$Sequence, qi, nonsense_error_rates_ecoli = nonsense_error_rates_ecoli)
  return(data)
}

In [24]:
data_ecoli <- add.qi(data_ecoli, nonsense_error_rates_ecoli)
data_ecoli_no_outliers <- add.qi(data_ecoli_no_outliers, nonsense_error_rates_ecoli)

In [25]:
data_ecoli
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

In [26]:
add.total.prod <- function(data, energy_expenditure, prod_q1, qi){
  data$total_prod <- data$energy_expenditure * data$prod_q1 * data$qi
  return(data)
}

In [27]:
data_ecoli <- add.total.prod(data_ecoli, energy_expenditure, prod_q1, qi)
data_ecoli_no_outliers <- add.total.prod(data_ecoli_no_outliers, energy_expenditure, prod_q1, qi)

In [28]:
data_ecoli
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

In [29]:
# Source the functions
source("utils.R")

In [30]:
# Call the necessary functions to compute r values
data_ecoli <- add.success.rate.col(data_ecoli, nonsense_error_rates_ecoli = nonsense_error_rates_ecoli)
data_ecoli_no_outliers <- add.success.rate.col(data_ecoli_no_outliers, nonsense_error_rates_ecoli = nonsense_error_rates_ecoli)

In [31]:
success_rate_wt <- translation.success.rate.of.mRNA(sequence_constructs[sequence_constructs$sequence_id == "V015", "Sequence"], nonsense_error_rates_ecoli)
data_ecoli <- add.r.column(data_ecoli, success_rate_wt)
data_ecoli_no_outliers <- add.r.column(data_ecoli_no_outliers, success_rate_wt)

Computing alpha values

In [32]:
source("sequence_conversions.R")

# This function computes the total elongation time 
# of an mRNA sequence from the codons of that sequence (argument: sequence) 
# and the elongation times for each individual codon of said sequence.
# Elongation times are sourced from a reference table ("elong_time_table").
# Elongation times of all threes stop codons are excluded.
total.elongation.time.of.mRNA <- function(seq_cand, elong_time_table, verbose = FALSE) {
  codons_of_sequence <- seq.string.to.cod.string(seq_cand)
  L <- length(codons_of_sequence)
  
  if (verbose) {
    cat("length candidate sequence is:", L, '\n')
  }
  
  # Exclude the last codon (stop codon)
  codons <- codons_of_sequence[1:(L-1)]
  
  # Identify positions of codons in the elongation time table
  positions_in_table <- match(codons, names(elong_time_table))
  
  # Retrieve elongation times for codons
  elong_times <- elong_time_table[positions_in_table]
  
  if (verbose) {
    cat("Elongation times of the codons:", elong_times, '\n')
  }
  
  # Calculate total elongation time
  total_elon_time <- sum(elong_times)
  
  return(total_elon_time)
}

In [33]:
# Write a function to add elongation times column to dataframe
add.elongation.time.col <- function(data, elong_time_table){
  data$elongation_times <- sapply(data$Sequence, total.elongation.time.of.mRNA, elong_time_table = elong_time_table)
  return(data)
}
# Call the function add.elongation.time.col
data_ecoli <- add.elongation.time.col(data_ecoli, elongation_times_ecoli)
data_ecoli_no_outliers <- add.elongation.time.col(data_ecoli_no_outliers, elongation_times_ecoli)

In [34]:
# Call the necessary functions to compute alpha values
# id = 15 is the wildtype
# add the corresponding sequence from data_ecoli$Sequence to the id_wt vector

# Write a function to calculate alpha values
calculate.alpha <- function(data, strain) {
  wt_strain <- data[data$sequence_id == 'V015' & data$strain == strain,]
  alpha <- wt_strain$mean_fluorescence * wt_strain$elongation_times
  # multiple equal values in the vector, so take the first one
  return(alpha[1])
}

add.alpha.col <- function(data){
  alpha_k12 <- calculate.alpha(data_ecoli, "K12")
  alpha_b21 <- calculate.alpha(data_ecoli, "BL21DE3")

  # add the alpha values to the dataframe based on the strain
  data$alpha <- ifelse(data$strain == "K12", alpha_k12, alpha_b21)
  return(data)
}

data_ecoli <- add.alpha.col(data_ecoli)
data_ecoli_no_outliers <- add.alpha.col(data_ecoli_no_outliers)


In [35]:
head(data_ecoli)
head(data_ecoli_no_outliers)

sequence_id sequence_name strain  value    mean_fluorescence
1 V015        V015-wildtype BL21DE3 16486.75 17098.38         
2 V015        V015-wildtype BL21DE3 16621.75 17098.38         
3 V015        V015-wildtype BL21DE3 17863.75 17098.38         
4 V015        V015-wildtype BL21DE3 13851.75 17098.38         
5 V015        V015-wildtype BL21DE3 19477.00 17098.38         
6 V015        V015-wildtype BL21DE3 19002.00 17098.38         
  Sequence                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
2 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
3 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTG

sequence_id sequence_name strain  value    mean_fluorescence
1 V015        V015-wildtype BL21DE3 16486.75 17098.38         
2 V015        V015-wildtype BL21DE3 16621.75 17098.38         
3 V015        V015-wildtype BL21DE3 17863.75 17098.38         
4 V015        V015-wildtype BL21DE3 13851.75 17098.38         
5 V015        V015-wildtype BL21DE3 19477.00 17098.38         
6 V015        V015-wildtype BL21DE3 19002.00 17098.38         
  Sequence                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
2 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
3 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTG

In [36]:
calculate.b <- function(data, strain) {
  wt_strain <- data[data$sequence_id == 'V015' & data$strain == strain,]
  b_value <- (wt_strain$r * wt_strain$alpha) / (wt_strain$mean_fluorescence * 2)
  # multiple equal values in the vector, so take the first one
  return(b_value[1])
}

add.b.col <- function(data){
  b_k12 <- calculate.b(data_ecoli, "K12")
  b_b21 <- calculate.b(data_ecoli, "BL21DE3")

  # add the alpha values to the dataframe based on the strain
  data$b <- ifelse(data$strain == "K12", b_k12, b_b21)
  return(data)
}

data_ecoli <- add.b.col(data_ecoli)
data_ecoli_no_outliers <- add.b.col(data_ecoli_no_outliers)

In [37]:
data_ecoli
head(data_ecoli_no_outliers)

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name strain  value    mean_fluorescence
1 V015        V015-wildtype BL21DE3 16486.75 17098.38         
2 V015        V015-wildtype BL21DE3 16621.75 17098.38         
3 V015        V015-wildtype BL21DE3 17863.75 17098.38         
4 V015        V015-wildtype BL21DE3 13851.75 17098.38         
5 V015        V015-wildtype BL21DE3 19477.00 17098.38         
6 V015        V015-wildtype BL21DE3 19002.00 17098.38         
  Sequence                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
2 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTGGCATCCTCTCTCCTTACACTTACACTCTTAGAGAGACTGGACCAGAGGATGTGAACATAAGAATCATTTGCTGTGGAATCTGCCACACCGATCTTCATCAAACTAAAAATGATCTTGGCATGTCTAATTACCCCATGGTTCCTGGGCATGAAGTGGTAGGGGAAGTAGTGGAGGTGGGATCAGATGTGAGCAAGTTCACCGTAGGGGACATAGTTGGAGTTGGTTGCCTCGTTGGATGTTGCGGAGGTTGTAGCCCCTGCGAGAGAGATCTGGAACAGTATTGTCCAAAGAAGATTTGGAGCTACAATGATGTTTACATCAATGGTCAACCTACACAAGGCGGCTTCGCTAAAGCCACCGTCGTTCACCAAAAGTTTGTGGTCAAGATTCCAGAAGGAATGGCGGTTGAGCAGGCTGCGCCGCTACTGTGCGCTGGTGTGACTGTGTACAGTCCACTGAGCCACTTTGGTCTGAAACAACCAGGCCTAAGAGGAGGTATACTAGGGTTAGGTGGAGTCGGTCACATGGGTGTGAAAATAGCCAAAGCAATGGGTCACCATGTGACTGTCATAAGCTCATCAAACAAGAAGAGAGAAGAGGCATTGCAAGATCTTGGAGCTGATGATTACGTGATCGGTTCCGACCAAGCGAAGATGAGCGAATTGGCTGATTCGTTGGATTACGTAATTGACACGGTGCCTGTTCATCATGCACTTGAGCCATATTTGTCTCTGCTTAAGCTTGATGGTAAACTCATTCTCATGGGAGTTATCAACAATCCATTACAGTTTCTCACTCCTCTGCTTATGCTTGGGAGGAAAGTGATAACGGGGAGCTTCATAGGGAGCATGAAGGAGACAGAGGAGATGCTTGAGTTCTGTAAAGAAAAGGGTTTGAGTTCGATTATCGAAGTTGTGAAGATGGATTATGTTAACACTGCGTTTGAGAGACTTGAGAAGAACGATGTGCGTTATAGGTTCGTCGTTGATGTCGAAGGAAGCAATCTCGACGCTTTAATTGGCTCCGATGGAGGGTCTGGTGGCGGATCAACAAGTCGTGACCACATGGTCCTTCATGAGTACGTAAATGCTGCTGGGATTACATGA
3 ATGGGAATAATGGAGGCAGAGAGGAAAACAACAGGCTGGGCTGCCAGAGACCCATCTG

#### Compute equation

In [38]:
# Write the equation from the paper to calculate eta
# eta = (1/b) * pord_q1 * qi * energy_expenditure
data_ecoli$eta <- (1/data_ecoli$b) * data_ecoli$total_prod
data_ecoli_no_outliers$eta <- (1/data_ecoli_no_outliers$b) * data_ecoli_no_outliers$prod_q1 * data_ecoli_no_outliers$qi * data_ecoli_no_outliers$energy_expenditure
data_ecoli



sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

#### Write equation to calculate protein expression rate (phi) prediction

In [39]:
# Compute phi values
# phi = 1/eta
data_ecoli$phi <- 1/data_ecoli$eta
data_ecoli_no_outliers$phi <- 1/data_ecoli_no_outliers$eta
data_ecoli
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

In [40]:
# Write a function that computes predicted protein level and adds it to the dataframe
# predicted protein level = phi * elongation time
predicted.protein.level <- function(data){
  data$predicted_level <- data$phi * data$elongation_times
  return(data)
}

In [41]:
data_ecoli <- predicted.protein.level(data_ecoli)
data_ecoli_no_outliers <- predicted.protein.level(data_ecoli_no_outliers)
data_ecoli
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

#### Create dataframes for model evaluation and plotting

In [42]:
# Create a dataframe with only the columns of interest sequence_name, strain, value, mean_flourescence, predicted_protein_level
data_ecoli <- data_ecoli[,c(1,2,3,4,5,18)]
data_ecoli

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14075.00         
10  V015        V015-wildtype          K12     14101.50 14075.00         
11  V015        V015-wildtype          K12     15070.50 14075.00         
12  V015        V015-wildtype          K12     14050.50 14075.00         
13  V015        V015-wildtype          K12     14740.00 14075.00         
14  V015        V015-wildtype          K12     14743.00 14075.00         
15  V015        V015-wildtype          K12     13430.00 14075.00         
16  V015        V015-wildtype          K12     11611.00 14075.00         
17  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
21  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
24  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
25  V016        V016-AnaCoda           K12     21446.50 20681.00         
26  V016        V016-AnaCoda           K12     21939.50 20681.00         
27  V016        V016-AnaCoda           K12     24331.50 20681.00         
28  V016        V016-AnaCoda           K12     20637.50 20681.00         
29  V016        V016-AnaCoda           K12     20591.00 20681.00         
30  V016        V016-AnaCoda           K12     20112.00 20681.00         
... ...         ...                    ...     ...      ...              
267 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.62         
268 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.62         
269 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.62         
270 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.62         
271 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.62         
272 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.62         
273 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.88         
274 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.88         
275 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.88         
276 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.88         
277 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.88         
278 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.88         
279 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.88         
280 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.88         
281 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25167.88         
282 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25167.88         
283 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25167.88         
284 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25167.88         
285 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25167.88         
286 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25167.88         
287 V036        V036-RTCIM (Variant 2) BL21DE3 24419.00 25167.88         
288 V036        V036-RTCIM (Variant 2) BL21DE3 21393.00 25167.88         
289 V037

In [43]:
data_ecoli_no_outliers <- data_ecoli_no_outliers[,c(1,2,3,4,5,18)]
data_ecoli_no_outliers

sequence_id sequence_name          strain  value    mean_fluorescence
1   V015        V015-wildtype          BL21DE3 16486.75 17098.38         
2   V015        V015-wildtype          BL21DE3 16621.75 17098.38         
3   V015        V015-wildtype          BL21DE3 17863.75 17098.38         
4   V015        V015-wildtype          BL21DE3 13851.75 17098.38         
5   V015        V015-wildtype          BL21DE3 19477.00 17098.38         
6   V015        V015-wildtype          BL21DE3 19002.00 17098.38         
7   V015        V015-wildtype          BL21DE3 19599.00 17098.38         
8   V015        V015-wildtype          BL21DE3 13885.00 17098.38         
9   V015        V015-wildtype          K12     14853.50 14427.00         
10  V015        V015-wildtype          K12     14101.50 14427.00         
11  V015        V015-wildtype          K12     15070.50 14427.00         
12  V015        V015-wildtype          K12     14050.50 14427.00         
13  V015        V015-wildtype          K12     14740.00 14427.00         
14  V015        V015-wildtype          K12     14743.00 14427.00         
15  V015        V015-wildtype          K12     13430.00 14427.00         
16  V016        V016-AnaCoda           BL21DE3 32716.75 33182.50         
17  V016        V016-AnaCoda           BL21DE3 31710.75 33182.50         
18  V016        V016-AnaCoda           BL21DE3 30605.75 33182.50         
19  V016        V016-AnaCoda           BL21DE3 34179.75 33182.50         
20  V016        V016-AnaCoda           BL21DE3 34453.00 33182.50         
21  V016        V016-AnaCoda           BL21DE3 35672.00 33182.50         
22  V016        V016-AnaCoda           BL21DE3 34050.00 33182.50         
23  V016        V016-AnaCoda           BL21DE3 32072.00 33182.50         
24  V016        V016-AnaCoda           K12     21446.50 20584.75         
25  V016        V016-AnaCoda           K12     21939.50 20584.75         
26  V016        V016-AnaCoda           K12     20637.50 20584.75         
27  V016        V016-AnaCoda           K12     20591.00 20584.75         
28  V016        V016-AnaCoda           K12     20112.00 20584.75         
29  V016        V016-AnaCoda           K12     18782.00 20584.75         
30  V017        V017-GeneGA            BL21DE3 31330.75 33211.04         
... ...         ...                    ...     ...      ...              
237 V035        V035-RTCIM (Variant 1) BL21DE3 24156.75 23893.625        
238 V035        V035-RTCIM (Variant 1) BL21DE3 25186.75 23893.625        
239 V035        V035-RTCIM (Variant 1) BL21DE3 22986.75 23893.625        
240 V035        V035-RTCIM (Variant 1) BL21DE3 21332.75 23893.625        
241 V035        V035-RTCIM (Variant 1) BL21DE3 24529.00 23893.625        
242 V035        V035-RTCIM (Variant 1) BL21DE3 26871.00 23893.625        
243 V035        V035-RTCIM (Variant 1) BL21DE3 25056.00 23893.625        
244 V035        V035-RTCIM (Variant 1) BL21DE3 21030.00 23893.625        
245 V035        V035-RTCIM (Variant 1) K12     17575.50 16535.875        
246 V035        V035-RTCIM (Variant 1) K12     17084.50 16535.875        
247 V035        V035-RTCIM (Variant 1) K12     18205.50 16535.875        
248 V035        V035-RTCIM (Variant 1) K12     17276.50 16535.875        
249 V035        V035-RTCIM (Variant 1) K12     15079.00 16535.875        
250 V035        V035-RTCIM (Variant 1) K12     15021.00 16535.875        
251 V035        V035-RTCIM (Variant 1) K12     14710.00 16535.875        
252 V035        V035-RTCIM (Variant 1) K12     17335.00 16535.875        
253 V036        V036-RTCIM (Variant 2) BL21DE3 25803.75 25707.143        
254 V036        V036-RTCIM (Variant 2) BL21DE3 26853.75 25707.143        
255 V036        V036-RTCIM (Variant 2) BL21DE3 25493.75 25707.143        
256 V036        V036-RTCIM (Variant 2) BL21DE3 27375.75 25707.143        
257 V036        V036-RTCIM (Variant 2) BL21DE3 25545.00 25707.143        
258 V036        V036-RTCIM (Variant 2) BL21DE3 24459.00 25707.143        
259 V036

In [44]:
# Write csv files for plotting
write.csv(data_ecoli, file = "dataframes/efficacy_accuracy/data_ecoli.csv")
write.csv(data_ecoli_no_outliers, file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers.csv")

# Write s csv file of each dataframe and each strain
write.csv(data_ecoli[data_ecoli$strain == "K12",], file = "dataframes/efficacy_accuracy/data_ecoli_K12.csv")
write.csv(data_ecoli[data_ecoli$strain == "BL21DE3",], file = "dataframes/efficacy_accuracy/data_ecoli_BL21DE3.csv")
# dataframe with no outliers
write.csv(data_ecoli_no_outliers[data_ecoli_no_outliers$strain == "K12",], file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers_K12.csv")
write.csv(data_ecoli_no_outliers[data_ecoli_no_outliers$strain == "BL21DE3",], file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers_BL21DE3.csv")

In [ ]:
# Group the dataframes by mean_fluorescence and predicted_level
data_ecoli_averaged <- aggregate(cbind(mean_fluorescence, predicted_level) ~ sequence_name + strain, data = data_ecoli, FUN = mean)
data_ecoli_averaged

# Group the dataframes by mean_fluorescence and predicted_level in dataframe with no outliers
data_ecoli_no_outliers_averaged <- aggregate(cbind(mean_fluorescence, predicted_level) ~ sequence_name + strain, data = data_ecoli_no_outliers, FUN = mean)
data_ecoli_no_outliers_averaged

In [47]:
# Write a csv file with the dataframes
write.csv(data_ecoli_averaged, file = "dataframes/efficacy_accuracy/data_ecoli_averaged.csv")
write.csv(data_ecoli_no_outliers_averaged, file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers_averaged.csv")

# Write s csv file of each dataframe and each strain
write.csv(data_ecoli_averaged[data_ecoli_averaged$strain == "K12",], file = "dataframes/efficacy_accuracy/data_ecoli_averaged_K12.csv")
write.csv(data_ecoli_averaged[data_ecoli_averaged$strain == "BL21DE3",], file = "dataframes/efficacy_accuracy/data_ecoli_averaged_BL21DE3.csv")
# dataframe with no outliers
write.csv(data_ecoli_no_outliers_averaged[data_ecoli_no_outliers_averaged$strain == "K12",], file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers_averaged_K12.csv")
write.csv(data_ecoli_no_outliers_averaged[data_ecoli_no_outliers_averaged$strain == "BL21DE3",], file = "dataframes/efficacy_accuracy/data_ecoli_no_outliers_averaged_BL21DE3.csv")